# Strategia in tempo reale: contrarian

Iniziamo con una strategia semplice, la strategia **contrarian**

In [1]:
import pandas as pd
import numpy as np
import time
from datetime import datetime, timedelta, timezone
import tpqoa

In [2]:
class Trader(tpqoa.tpqoa):
    
    def __init__(self,config_file, instrument, period, window):
        super().__init__(config_file)
        self.instrument = instrument
        self.period=period
        self.tickData = pd.DataFrame()
        self.rawData = None 
        self.ultimoPeriodo = None 
        
        self.data = None
        ########################## STRATEGY SPECIFIC ATTRIBUTES ##############################
        self.window = window
        
    def getMostRecent(self, days=5): 
        '''questo metodo scarica i dati FINO ad adesso'''
        while True:
            now = datetime.now(timezone.utc)
            now = now - timedelta(microseconds = now.microsecond) # pay attention, microseconds and then microsecond (singular!!!)
            yesterday = now - timedelta(days= days) # lo chiamo YESTERDAY, ma è l'inizio del periodo da scaricare
            df = self.get_history(instrument = self.instrument, start = str(yesterday)[:-6], end = str(now)[:-6],
                        granularity= "S5", price="M", localize=False)["c"].to_frame() 
                        # scarico a 5secondi, il che vuol dire che period non può essere più corto!
            df.rename(columns={"c":self.instrument},inplace=True)
            self.rawData = df.resample(self.period, label="right").last().dropna().iloc[:-1]
            self.ultimoPeriodo = self.rawData.index[-1]
            if pd.to_datetime(datetime.now(timezone.utc)) - self.ultimoPeriodo < pd.to_timedelta(self.period):
                break
            else:
                time.sleep(2)
    
    def on_success(self, time, bid, ask):
#        print(time, bid, ask)
        print(self.ticks, end=" ")
        tickCorrente = pd.to_datetime(time)
        df = pd.DataFrame({self.instrument:(ask+bid)/2}, index=[tickCorrente])
        self.tickData=pd.concat((self.tickData,df),axis=0)
        if tickCorrente - self.ultimoPeriodo > pd.to_timedelta(self.period):
            self.resampleJoin()
            # NEW
            self.defineStrategy()
    
    def resampleJoin(self):
        self.rawData=pd.concat((self.rawData,self.tickData.resample(self.period,label="right").last().ffill().iloc[:-1] ),axis=0)
        self.tickData = self.tickData.iloc[-1:] 
        self.ultimoPeriodo = self.rawData.index[-1] 
        
    def defineStrategy(self):
        df = self.rawData.copy()
        df["logRet"]=np.log(df[self.instrument] / df[self.instrument].shift(1))
        df["posizione"]= - np.sign(df.logRet.rolling(self.window).mean())
        # ogni volta mi ricalcolo logRet e la posizione per TUTTI gli intervalli (candele), cosa che quando l'algoritmo
        # gira per lungo tempo diventa molto inefficiente, basterebbe calcolarlo solo per l'ultimo
        self.data = df.copy()
        

In [3]:
trader = Trader("oandaMY.cfg","EUR_USD","1min", window=1)

In [4]:
print(datetime.now(timezone.utc))
trader.getMostRecent()
trader.stream_data(trader.instrument,stop=50)

2024-11-18 08:39:18.821170+00:00


C:\ProgramData\anaconda3\Lib\site-packages\tpqoa\tpqoa.py:223: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  dr = pd.date_range(start, end, freq=freq)


1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 

In [5]:
trader.rawData

EUR_USD
2024-11-13 08:40:00+00:00  1.06070
2024-11-13 08:41:00+00:00  1.06066
2024-11-13 08:42:00+00:00  1.06056
2024-11-13 08:43:00+00:00  1.06050
2024-11-13 08:44:00+00:00  1.06050
...                            ...
2024-11-18 08:36:00+00:00  1.05455
2024-11-18 08:37:00+00:00  1.05483
2024-11-18 08:38:00+00:00  1.05476
2024-11-18 08:39:00+00:00  1.05478
2024-11-18 08:40:00+00:00  1.05478

[4304 rows x 1 columns]

In [6]:
trader.data

EUR_USD    logRet  posizione
2024-11-13 08:40:00+00:00  1.06070       NaN        NaN
2024-11-13 08:41:00+00:00  1.06066 -0.000038        1.0
2024-11-13 08:42:00+00:00  1.06056 -0.000094        1.0
2024-11-13 08:43:00+00:00  1.06050 -0.000057        1.0
2024-11-13 08:44:00+00:00  1.06050  0.000000       -0.0
...                            ...       ...        ...
2024-11-18 08:36:00+00:00  1.05455 -0.000066        1.0
2024-11-18 08:37:00+00:00  1.05483  0.000265       -1.0
2024-11-18 08:38:00+00:00  1.05476 -0.000066        1.0
2024-11-18 08:39:00+00:00  1.05478  0.000019       -1.0
2024-11-18 08:40:00+00:00  1.05478  0.000000       -0.0

[4304 rows x 3 columns]

# Come inserire ordini in OANDA

In [7]:
import pandas as pd
import tpqoa
api=tpqoa.tpqoa("oandaMY.cfg")

In [8]:
#api.create_order(instrument = "EUR_USD", units = 100000, sl_distance= 0.1, tp_price=1.18, price=1.13)
api.create_order(instrument = "EUR_USD", units = 100000, sl_distance= 0.1)



 {'id': '610', 'time': '2024-11-18T08:40:08.831466924Z', 'userID': 27030320, 'accountID': '101-011-27030320-002', 'batchID': '609', 'requestID': '61307391192899635', 'type': 'ORDER_FILL', 'orderID': '609', 'instrument': 'EUR_USD', 'units': '100000.0', 'gainQuoteHomeConversionFactor': '0.94323972647', 'lossQuoteHomeConversionFactor': '0.952719522716', 'price': 1.05493, 'fullVWAP': 1.05493, 'fullPrice': {'type': 'PRICE', 'bids': [{'price': 1.05482, 'liquidity': '500000'}, {'price': 1.05481, 'liquidity': '2500000'}, {'price': 1.0548, 'liquidity': '2000000'}, {'price': 1.05479, 'liquidity': '5000000'}, {'price': 1.05476, 'liquidity': '10000000'}, {'price': 1.05473, 'liquidity': '10000000'}], 'asks': [{'price': 1.05493, 'liquidity': '500000'}, {'price': 1.05494, 'liquidity': '500000'}, {'price': 1.05495, 'liquidity': '2000000'}, {'price': 1.05496, 'liquidity': '2000000'}, {'price': 1.05497, 'liquidity': '5000000'}, {'price': 1.05499, 'liquidity': '10000000'}, {'price': 1.05502, 'liquidity

In [9]:
api.get_positions()

[]

In [10]:
api.get_transactions(tid = 199-1)

[{'id': '199',
  'time': '2023-11-21T22:52:00.350847636Z',
  'userID': 27030320,
  'accountID': '101-011-27030320-002',
  'batchID': '199',
  'requestID': '25147261758156342',
  'type': 'MARKET_ORDER',
  'instrument': 'EUR_USD',
  'units': '-100000.0',
  'timeInForce': 'FOK',
  'positionFill': 'DEFAULT',
  'reason': 'CLIENT_ORDER'},
 {'id': '200',
  'time': '2023-11-21T22:52:00.350847636Z',
  'userID': 27030320,
  'accountID': '101-011-27030320-002',
  'batchID': '199',
  'requestID': '25147261758156342',
  'type': 'ORDER_FILL',
  'orderID': '199',
  'instrument': 'EUR_USD',
  'units': '-100000.0',
  'gainQuoteHomeConversionFactor': '0.911802588079',
  'lossQuoteHomeConversionFactor': '0.920966433185',
  'price': 1.09114,
  'fullVWAP': 1.09114,
  'fullPrice': {'type': 'PRICE',
   'bids': [{'price': 1.09114, 'liquidity': '1000000'},
    {'price': 1.09113, 'liquidity': '2000000'},
    {'price': 1.09112, 'liquidity': '2000000'},
    {'price': 1.0911, 'liquidity': '5000000'}],
   'asks': [

In [11]:
api.print_transactions(tid = 199-1)

 200 | 2023-11-21T22:52:00.35 | EUR_USD | -100000.0 | -12.8935
 202 | 2023-11-21T22:53:21.97 | EUR_USD | -100000.0 | -14.7354
 204 | 2023-11-21T22:55:00.39 | EUR_USD | 200000.0 |      0.0
 206 | 2023-11-21T22:55:00.65 | EUR_USD | -100000.0 | -19.3412
 208 | 2023-11-21T22:56:04.55 | EUR_USD | -100000.0 | -14.7361
 210 | 2023-11-21T22:58:03.43 | EUR_USD | 200000.0 |      0.0
 212 | 2023-11-21T23:00:00.59 | EUR_USD | -100000.0 | -28.5549
 214 | 2023-11-21T23:01:04.90 | EUR_USD | -100000.0 |  -3.6838
 216 | 2023-11-21T23:04:10.46 | EUR_USD | 200000.0 |      0.0
 218 | 2023-11-21T23:04:33.55 | EUR_USD | -100000.0 |  20.9659
 222 | 2023-11-24T08:37:00.26 | EUR_USD |  10000.0 |      0.0
 224 | 2023-11-24T08:38:01.16 | EUR_USD | -20000.0 | -14.7421
 226 | 2023-11-24T08:40:00.49 | EUR_USD |  20000.0 |      0.0
 228 | 2023-11-24T08:40:04.01 | EUR_USD | -10000.0 |  -6.5413
 530 | 2024-09-18T13:31:47.87 | EUR_USD | -100000.0 | 1981.5307
 532 | 2024-09-18T13:33:14.09 | EUR_USD | 100000.0 |      0.0

In [12]:
api.create_order(instrument = "EUR_USD", units = -100000)



 {'id': '612', 'time': '2024-11-18T08:40:10.867633745Z', 'userID': 27030320, 'accountID': '101-011-27030320-002', 'batchID': '611', 'requestID': '61307391201290622', 'type': 'ORDER_FILL', 'orderID': '611', 'instrument': 'EUR_USD', 'units': '-100000.0', 'gainQuoteHomeConversionFactor': '0.943275493352', 'lossQuoteHomeConversionFactor': '0.952755649064', 'price': 1.05479, 'fullVWAP': 1.05479, 'fullPrice': {'type': 'PRICE', 'bids': [{'price': 1.05479, 'liquidity': '500000'}, {'price': 1.05478, 'liquidity': '2500000'}, {'price': 1.05477, 'liquidity': '2000000'}, {'price': 1.05476, 'liquidity': '5000000'}, {'price': 1.05473, 'liquidity': '10000000'}, {'price': 1.0547, 'liquidity': '10000000'}], 'asks': [{'price': 1.05488, 'liquidity': '400000'}, {'price': 1.05489, 'liquidity': '500000'}, {'price': 1.0549, 'liquidity': '2000000'}, {'price': 1.05491, 'liquidity': '2000000'}, {'price': 1.05492, 'liquidity': '5000000'}, {'price': 1.05494, 'liquidity': '10000000'}, {'price': 1.05497, 'liquidit

In [13]:
api.get_positions()

[{'instrument': 'EUR_USD',
  'pl': '3796.0181',
  'unrealizedPL': '-9.5275',
  'marginUsed': '3333.3333',
  'resettablePL': '3796.0181',
  'financing': '-2923.7247',
  'commission': '0.0',
  'guaranteedExecutionFees': '0.0',
  'long': {'units': '0.0',
   'pl': '2179.5909',
   'unrealizedPL': '0.0',
   'resettablePL': '2179.5909',
   'financing': '-2941.5604',
   'guaranteedExecutionFees': '0.0'},
  'short': {'units': '-100000.0',
   'averagePrice': 1.05479,
   'tradeIDs': ['612'],
   'pl': '1616.4272',
   'unrealizedPL': '-9.5275',
   'resettablePL': '1616.4272',
   'financing': '17.8357',
   'guaranteedExecutionFees': '0.0'}}]

In [14]:
api.get_account_summary()

{'id': '101-011-27030320-002',
 'alias': 'Paolo',
 'currency': 'EUR',
 'balance': '100808.9332',
 'createdByUserID': 27030320,
 'createdTime': '2023-10-03T15:26:25.580818880Z',
 'guaranteedStopLossOrderMode': 'ALLOWED',
 'pl': '3732.6579',
 'resettablePL': '3732.6579',
 'resettablePLTime': '0',
 'financing': '-2923.7247',
 'commission': '0.0',
 'guaranteedExecutionFees': '0.0',
 'marginRate': '0.03333333333333',
 'openTradeCount': 1,
 'openPositionCount': 1,
 'pendingOrderCount': 0,
 'hedgingEnabled': False,
 'unrealizedPL': '-9.5275',
 'NAV': '100799.4057',
 'marginUsed': '3333.3333',
 'marginAvailable': '97470.8598',
 'positionValue': '100000.0',
 'marginCloseoutUnrealizedPL': '-4.7401',
 'marginCloseoutNAV': '100804.1931',
 'marginCloseoutMarginUsed': '3333.3333',
 'marginCloseoutPercent': '0.01653',
 'marginCloseoutPositionValue': '100000.0',
 'withdrawalLimit': '97470.8598',
 'marginCallMarginUsed': '3333.3333',
 'marginCallPercent': '0.03307',
 'lastTransactionID': '612'}

In [15]:
# order = api.create_order(instrument = "EUR_USD", units = 100000, sl_distance= 0.1, price=1.15, tp_price=1.18, suppress = True, ret= True) 
order = api.create_order(instrument = "EUR_USD", units = 100000, suppress = True, ret= True) 

In [16]:
order

{'id': '614',
 'time': '2024-11-18T08:40:11.346939059Z',
 'userID': 27030320,
 'accountID': '101-011-27030320-002',
 'batchID': '613',
 'requestID': '61307391205485493',
 'type': 'ORDER_FILL',
 'orderID': '613',
 'instrument': 'EUR_USD',
 'units': '100000.0',
 'gainQuoteHomeConversionFactor': '0.943271022831',
 'lossQuoteHomeConversionFactor': '0.952751133613',
 'price': 1.05489,
 'fullVWAP': 1.05489,
 'fullPrice': {'type': 'PRICE',
  'bids': [{'price': 1.05479, 'liquidity': '400000'},
   {'price': 1.05478, 'liquidity': '2500000'},
   {'price': 1.05477, 'liquidity': '2000000'},
   {'price': 1.05476, 'liquidity': '5000000'},
   {'price': 1.05473, 'liquidity': '10000000'},
   {'price': 1.0547, 'liquidity': '10000000'}],
  'asks': [{'price': 1.05489, 'liquidity': '400000'},
   {'price': 1.0549, 'liquidity': '500000'},
   {'price': 1.05491, 'liquidity': '2000000'},
   {'price': 1.05492, 'liquidity': '2000000'},
   {'price': 1.05493, 'liquidity': '5000000'},
   {'price': 1.05495, 'liquidity

In [17]:
order["units"]

'100000.0'

In [18]:
order["price"] # valid only if you specify a price in the order or if you do NOT specify TP SL prices

1.05489

In [19]:
order2 = api.create_order(instrument = "EUR_USD", units = -100000, suppress = True, ret= True) 

In [20]:
order2["price"]

1.05479

# Inserire ordini nella classe Trader

In [21]:
class Trader(tpqoa.tpqoa):
    
    def __init__(self,config_file, instrument, period, window, units):
        super().__init__(config_file)
        self.instrument = instrument
        self.period=period
        self.tickData = pd.DataFrame()
        self.rawData = None 
        self.ultimoPeriodo = None 
        self.data = None
        # NEW
        self.units = units
        # queste sono le unità che compriamo/vendiamo ad ogni cambio di posizione. Notare che sarebbe meglio
        # comprare e vendere un quantitativo fisso del NOSTRO DENARO e non di unità dello strumento
        self.posizione = 0
        
        ########################## STRATEGY SPECIFIC ATTRIBUTES ##############################
        self.window = window
        
    def getMostRecent(self, days=5): 
        '''questo metodo scarica i dati FINO ad adesso'''
        while True:
            now = datetime.now(timezone.utc)
            now = now - timedelta(microseconds = now.microsecond) # pay attention, microseconds and then microsecond (singular!!!)
            yesterday = now - timedelta(days= days) # lo chiamo YESTERDAY, ma è l'inizio del periodo da scaricare
            df = self.get_history(instrument = self.instrument, start = str(yesterday)[:-6], end = str(now)[:-6],
                        granularity= "S5", price="M", localize=False)["c"].to_frame() 
                        # scarico a 5secondi, il che vuol dire che period non può essere più corto!
            df.rename(columns={"c":self.instrument},inplace=True)
            self.rawData = df.resample(self.period, label="right").last().dropna().iloc[:-1]
            self.ultimoPeriodo = self.rawData.index[-1]
            if pd.to_datetime(datetime.now(timezone.utc)) - self.ultimoPeriodo < pd.to_timedelta(self.period):
                break
            else:
                time.sleep(2)
    
    def on_success(self, time, bid, ask):
        print(self.ticks, end=" ")
        tickCorrente = pd.to_datetime(time)
        df = pd.DataFrame({self.instrument:(ask+bid)/2}, index=[tickCorrente])
        self.tickData=pd.concat((self.tickData,df),axis=0)
        if tickCorrente - self.ultimoPeriodo > pd.to_timedelta(self.period):
            self.resampleJoin()
            self.defineStrategy()
            # NEW
            self.executeTrade()
    
    def resampleJoin(self):
        self.rawData=pd.concat((self.rawData,self.tickData.resample(self.period,label="right").last().ffill().iloc[:-1] ),axis=0)
        self.tickData = self.tickData.iloc[-1:] 
        self.ultimoPeriodo = self.rawData.index[-1] 
        
    def defineStrategy(self):
        df = self.rawData.copy()
        df["logRet"]=np.log(df[self.instrument] / df[self.instrument].shift(1))
        df["posizione"]= - np.sign(df.logRet.rolling(self.window).mean())
        # ogni volta mi ricalcolo logRet e la posizione per TUTTI gli intervalli (candele), cosa che quando l'algoritmo
        # gira per lungo tempo diventa molto inefficiente, basterebbe calcolarlo solo per l'ultimo
        self.data = df.copy()
        
    def executeTrade(self):
        if self.data.posizione.iloc[-1] == 1: # andiamo lunghi
            if self.posizione == 0:
                order = self.create_order(instrument = self.instrument, units = self.units, suppress=True, ret = True)
                print("VADO LUNGO",self.units,order["price"])
            elif self.posizione == -1:
                order = self.create_order(instrument = self.instrument, units = 2*self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE CORTA E VADO LUNGO",2*self.units,order["price"])
            self.posizione=1
        elif self.data.posizione.iloc[-1] == -1: # andiamo corti
            if self.posizione == 0:
                order = self.create_order(instrument = self.instrument, units = -self.units, suppress=True, ret = True)
                print("VADO CORTO",-self.units,order["price"])
            elif self.posizione == 1:
                order = self.create_order(instrument = self.instrument, units = -2*self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE LUNGA E VADO CORTO",-2*self.units,order["price"])
            self.posizione=-1
        elif self.data.posizione.iloc[-1] == 0: # andiamo neutri
            if self.posizione == 1:
                order = self.create_order(instrument = self.instrument, units = -self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE LUNGA",-self.units,order["price"])
            elif self.posizione == -1:
                order = self.create_order(instrument = self.instrument, units = self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE CORTA",self.units,order["price"])
            self.posizione=0
        

In [22]:
trader = Trader("oandaMY.cfg","EUR_USD","1min", window=1, units=100000)

In [23]:
print(datetime.now(timezone.utc))
trader.getMostRecent()
trader.stream_data(trader.instrument,stop=100)

2024-11-18 08:40:12.828255+00:00


C:\ProgramData\anaconda3\Lib\site-packages\tpqoa\tpqoa.py:223: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  dr = pd.date_range(start, end, freq=freq)


1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 VADO LUNGO 100000 1.05475
65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 